# COMPARE TO HUMANS

This notebook contains code to:
 - remove proper nouns and punctuation from human text ( CONTAINS STOPWORDS BEC USEFUL FOR PHRASES)
 - analyze phrases for word lists with Q ( shows how many proper nouns and makes removing new phrases resulting from removal of prop. nouns easier ) 
 - and without Q ( for the PMI socre to be accurate)
 

                            

In [1]:
import pandas as pd

In [22]:
df_reddit =pd.read_csv(r'C:\Users\Admin\HC3 EDA\reddit_filtered_dataset.csv')

In [23]:
df_reddit_human = df_reddit[df_reddit['Labels']==0]

In [24]:
df_reddit_human.drop(columns=['Labels'],inplace=True)

C:\Users\Admin\AppData\Local\Temp\ipykernel_24940\1010113288.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_reddit_human.drop(columns=['Labels'],inplace=True)


In [5]:
df_reddit_human

Data
0     Of course! The relevant passage is: "As to you...
1     I've actually written a bit about this before....
3     Incredible answer. This was very well sourced ...
5     That is generally what "foraging" implies. It ...
6     I find it difficult to impose any sort of rigi...
...                                                 ...
6504  You have fluid in your eyeballs. The added pre...
6506  Simply said: There aren't any awkward silences...
6507  There's this thing called brute forcing. That'...
6509  Pretty much. A small quick dip is all that the...
6510  Plastics contain lots of very tiny holes. When...

[5145 rows x 1 columns]

In [6]:
import nltk
from nltk import *

In [25]:
# clean reddit human
def preprocess(sent):
    sent = nltk.word_tokenize(sent)
    sent = nltk.pos_tag(sent)
    return sent

clean1 = []


try:
  for sentence in df_reddit_human["Data"]:

    # process sentences
    cleane = preprocess(sentence)
    clean1.append(cleane)

except KeyError:
  print("Column 'Data' not found")

In [8]:
clean1

[[('Of', 'IN'),
  ('course', 'NN'),
  ('!', '.'),
  ('The', 'DT'),
  ('relevant', 'JJ'),
  ('passage', 'NN'),
  ('is', 'VBZ'),
  (':', ':'),
  ('``', '``'),
  ('As', 'IN'),
  ('to', 'TO'),
  ('your', 'PRP$'),
  ('question', 'NN'),
  ('...', ':'),
  ('two', 'CD'),
  ('of', 'IN'),
  ('my', 'PRP$'),
  ('shops', 'NNS'),
  ('have', 'VBP'),
  ('fallen', 'VBN'),
  ('down', 'RB'),
  ('and', 'CC'),
  ('the', 'DT'),
  ('rest', 'NN'),
  ('are', 'VBP'),
  ('cracking', 'VBG'),
  ('.', '.'),
  ('So', 'RB'),
  ('not', 'RB'),
  ('only', 'RB'),
  ('the', 'DT'),
  ('tenants', 'NNS'),
  ('but', 'CC'),
  ('the', 'DT'),
  ('very', 'RB'),
  ('mice', 'RB'),
  ('have', 'VBP'),
  ('migrated', 'VBN'),
  ('.', '.'),
  ('Other', 'JJ'),
  ('people', 'NNS'),
  ('call', 'VBP'),
  ('this', 'DT'),
  ('a', 'DT'),
  ('misfortune', 'NN'),
  (',', ','),
  ('I', 'PRP'),
  ('do', 'VBP'),
  ("n't", 'RB'),
  ('call', 'VB'),
  ('it', 'PRP'),
  ('even', 'RB'),
  ('a', 'DT'),
  ('nuisance', 'NN'),
  ('.', '.'),
  ('Oh', 'UH'),
 

In [26]:
# reomve PRP$, ':'and "''" replace w q . ALso  '``' and "''" 
good_words =[]
for pair in clean1:

    for word, tag in pair:
        if tag != "NNP" and tag != ":" and tag != "''" and tag != "``" and tag != ".":
            good_words.append(word)

        elif tag == "NNP": 
            q = "Q"
            good_words.append(q)

        elif tag == ":":
            q = "T" 
            good_words.append(q)

        elif tag == ".":
            q = "T"
            good_words.append(q)



In [10]:
# without Q
good_words_Qless =[]
for pair in clean1:
    for word, tag in pair:
        if tag!= "NNP" and tag != ":" and tag != "''" and tag != "``" and tag != ".":
            good_words_Qless.append(word)

In [11]:
# lowercase words no Q
clean_words_Qless = []
for word in good_words_Qless:
    lowe = word.lower()
    clean_words_Qless.append(lowe)

In [27]:
# with T and Q
clean_words1 =[]
for word in good_words:
    if word != "Q" and word != "T":

        lowe= word.lower()
        clean_words1.append(lowe)
    elif word == "Q":
        q ="Q"
        clean_words1.append(q)
    elif word  == "T":
        q = "T"
        clean_words1.append(q)
    

In [13]:
# save no Q reddit human words clean
Qless_df = pd.DataFrame({'Word':clean_words_Qless})
Qless_df.to_csv("Q-less Reddit Human Cleanish Words.csv", index= False)

In [29]:
# save the reddit human clean to csv
red_df = pd.DataFrame({'Words':clean_words1})
red_df.to_csv("Q T Reddit Human.csv", index=False)

In [16]:
# Qless phrase analysis
# initialize collocation for reddit 'r' text
import nltk
from nltk.collocations import *

# init nltk measures
bigram_measures_r1_Qx = nltk.collocations.BigramAssocMeasures()
trigram_measures_r2_Qx = nltk.collocations.TrigramAssocMeasures()
quadgram_measures_r3_Qx = nltk.collocations.QuadgramAssocMeasures()

# find phrases 
finder_r1_Qx = BigramCollocationFinder.from_words(clean_words_Qless)
finder_r2_Qx= TrigramCollocationFinder.from_words(clean_words_Qless)
finder_r3_Qx =QuadgramCollocationFinder.from_words(clean_words_Qless)

# only phrases appearing 10+ times
finder_r1_Qx.apply_freq_filter(10)
finder_r2_Qx.apply_freq_filter(10)
finder_r3_Qx.apply_freq_filter(10)


# define phrase counts
bigram_freq_r1_Qx = finder_r1_Qx.ngram_fd.items()
trigram_freq_r2_Qx = finder_r2_Qx.ngram_fd.items()
quadgram_freq_r3_Qx = finder_r3_Qx.ngram_fd.items()

# define pmis
bigram_pmi_r1_Qx = [i for i in finder_r1_Qx.score_ngrams(bigram_measures_r1_Qx.pmi)]
trigram_pmi_r2_Qx = [i for i in finder_r2_Qx.score_ngrams(trigram_measures_r2_Qx.pmi)]
quadgram_pmi_r3_Qx = [i for i in finder_r3_Qx.score_ngrams(quadgram_measures_r3_Qx.pmi)]

# bigram list creation
pmi_list_r1_Qx =[]
count_list_r1_Qx =  []
phrase_list_r1_Qx =[]

for phrase , pmi in bigram_pmi_r1_Qx:
    for item in bigram_freq_r1_Qx:
        bigram, count = item
        if bigram == phrase:
            pmi_list_r1_Qx.append(pmi) # pmi for the bigram  = phrase
            count_list_r1_Qx.append(count)  # count for the phrase = bigram 
            phrase_list_r1_Qx.append(phrase) # phrase = bigram
            

#trigram list creation
pmi_list_r2_Qx = []
count_list_r2_Qx =[]
phrase_list_r2_Qx =[]

for phrase, pmi in trigram_pmi_r2_Qx:
    for item in trigram_freq_r2_Qx:
        bigram, count =item
        if bigram == phrase:
            pmi_list_r2_Qx.append(pmi)
            count_list_r2_Qx.append(count)
            phrase_list_r2_Qx.append(phrase)

# quadgram list creation
pmi_list_r3_Qx =[]
count_list_r3_Qx =[]
phrase_list_r3_Qx =[]

for phrase, pmi in quadgram_pmi_r3_Qx:
    for item in quadgram_freq_r3_Qx:
        quadgram, count =item
        if quadgram == phrase:
            pmi_list_r3_Qx.append(pmi)
            count_list_r3_Qx.append(count)
            phrase_list_r3_Qx.append(phrase)

In [18]:
# initialize collocation for reddit 'r' text
import nltk
from nltk.collocations import *

# init nltk measures
bigram_measures_r1 = nltk.collocations.BigramAssocMeasures()
trigram_measures_r2 = nltk.collocations.TrigramAssocMeasures()
quadgram_measures_r3 = nltk.collocations.QuadgramAssocMeasures()

# find phrases 
finder_r1 = BigramCollocationFinder.from_words(clean_words1)
finder_r2 = TrigramCollocationFinder.from_words(clean_words1)
finder_r3 =QuadgramCollocationFinder.from_words(clean_words1)

# only phrases appearing 10+ times
finder_r1.apply_freq_filter(10)
finder_r2.apply_freq_filter(10)
finder_r3.apply_freq_filter(10)


# define phrase counts
bigram_freq_r1 = finder_r1.ngram_fd.items()
trigram_freq_r2 = finder_r2.ngram_fd.items()
quadgram_freq_r3 = finder_r3.ngram_fd.items()

# define pmis
bigram_pmi_r1 = [i for i in finder_r1.score_ngrams(bigram_measures_r1.pmi)]
trigram_pmi_r2 = [i for i in finder_r2.score_ngrams(trigram_measures_r2.pmi)]
quadgram_pmi_r3 = [i for i in finder_r3.score_ngrams(quadgram_measures_r3.pmi)]

# bigram list creation
pmi_list_r1 =[]
count_list_r1 =  []
phrase_list_r1 =[]

for phrase , pmi in bigram_pmi_r1:
    for item in bigram_freq_r1:
        bigram, count = item
        if bigram == phrase:
            pmi_list_r1.append(pmi) # pmi for the bigram  = phrase
            count_list_r1.append(count)  # count for the phrase = bigram 
            phrase_list_r1.append(phrase) # phrase = bigram
            

#trigram list creation
pmi_list_r2 = []
count_list_r2 =[]
phrase_list_r2 =[]

for phrase, pmi in trigram_pmi_r2:
    for item in trigram_freq_r2:
        bigram, count =item
        if bigram == phrase:
            pmi_list_r2.append(pmi)
            count_list_r2.append(count)
            phrase_list_r2.append(phrase)

# quadgram list creation
pmi_list_r3 =[]
count_list_r3 =[]
phrase_list_r3 =[]

for phrase, pmi in quadgram_pmi_r3:
    for item in quadgram_freq_r3:
        quadgram, count =item
        if quadgram == phrase:
            pmi_list_r3.append(pmi)
            count_list_r3.append(count)
            phrase_list_r3.append(phrase)

In [19]:
# create dataframes
df_bigram_r1 = pd.DataFrame({'Phrase':phrase_list_r1 , 'Count':count_list_r1 , 'PMI':pmi_list_r1}) 
df_trigram_r2 = pd.DataFrame({'Phrase':phrase_list_r2 , 'Count': count_list_r2 , 'PMI':pmi_list_r2}) 
df_quadgram_r3 = pd.DataFrame({'Phrase':phrase_list_r3 , 'Count': count_list_r3 , 'PMI': pmi_list_r3})



In [47]:
# dataframes for Qless DO NOT RUN ALL , RUN Qless CODEBLOCK ABOVE, THEN THIS 
df_bigram_r1_Qx = pd.DataFrame({'Phrase':phrase_list_r1_Qx,'Count':count_list_r1_Qx, 'PMI':pmi_list_r1_Qx}) # kept same variable names and ran Qless code block right before 
df_trigram_r2_Qx = pd.DataFrame({'Phrase':phrase_list_r2_Qx,'Count':count_list_r2_Qx,'PMI': pmi_list_r2_Qx})
df_quadgram_r3_Qx = pd.DataFrame({'Phrase':phrase_list_r3_Qx,'Count': count_list_r3_Qx, 'PMI': pmi_list_r3_Qx})

# Essays

In [14]:
df_essay = pd.read_csv(r"C:\Users\Admin\student vs gpt essays.csv")

In [15]:
df_essay


id                                               text  \
0     6060D28C05B6  Some schools in United States ofter classes fr...   
1     60623DB5DE7A  Four-day work week, a remarkable idea to conse...   
2     607A39D981DE  Students and their families should consider an...   
3     60ACDFA1609E  Agree you will never grow if something beyond ...   
4     60AE13D3F07B  I think our character traits are formed by inf...   
...            ...                                                ...   
2416  F5FF5E9E553C  On september 2, 2015 Generic_Name was entering...   
2417  F60545D8271E  I think that schools must have a after school ...   
2418  F610B3CBF3DF  Winston Churchill once said "success consists ...   
2419  F610C7BCD9EC  Technology seems to be becoming more and more ...   
2420  F6194DEBEFA7  Teenage is a part of life where everyone wants...   

                                           instructions  \
0     \nTask: Write a persuasive essay on whether or...   
1     \nTask: Research the advantages and disadvanta...   
2     \nTask: \n\n1. Talk to your parents before tak...   
3     \nTask: Write an essay discussing the benefits...   
4     \nTask: Research and discuss how character tra...   
...                                                 ...   
2416  \nTask: Research different kinds of medical pr...   
2417  \nTask: Write an essay discussing why schools ...   
2418  \nTask: Write an essay about how having a few ...   
2419  \nTask: \n\nWrite an essay exploring the pros ...   
2420  \nTask: Analyze and explore the benefits of im...   

                                            source_text  
0     \nWhen considering the pros and cons of attend...  
1     \nOne of the primary arguments for implementin...  
2     \nBefore making any decisions about getting in...  
3     \nRalph Waldo Emerson once said, "Go confident...  
4     \nHuman character traits are shaped by a wide ...  
...                                                 ...  
2416  \nBecoming a surgeon requires a great deal of ...  
2417  \nSchools should offer an after school homewor...  
2418  \nIt’s human nature to be afraid to make mista...  
2419  \nOne of the main debates of 2020 for many stu...  
2420  \nThe implementation of a curfew for teenagers...  

[2421 rows x 4 columns]

In [16]:
human_essay = df_essay['text']

In [17]:
# clean essay 

def preprocess(sent):
    sent = nltk.word_tokenize(sent)
    sent = nltk.pos_tag(sent)
    return sent

clean2 = []


try:
  for sentence in human_essay:

    # process sentences
    cleane = preprocess(sentence)
    clean2.append(cleane)

except KeyError:
  print("Column 'Data' not found")


In [18]:
# with T and Q 
good_words2 =[]
for pair in clean2:

    for word, tag in pair:
        if tag != "NNP" and tag != ":" and tag != "''" and tag != "``" and tag != ".":
            good_words2.append(word)

        elif tag == "NNP": 
            q = "Q"
            good_words2.append(q)

        elif tag == ":":
            q = "T" 
            good_words2.append(q)

        elif tag == ".":
            q = "T"
            good_words2.append(q)

In [26]:
# no Q

good_words2_Qless =[]
for pair in clean2:
    for word, tag in pair:
        if tag != "NNP" and tag != ":" and tag != "''" and tag != "``" and tag != ".":
            good_words2_Qless.append(word) 


In [19]:
clean_words2 =[]
for word in good_words2:
    if word != "Q" and word != "T":

        lowe= word.lower()
        clean_words2.append(lowe)
    elif word == "Q":
        q ="Q"
        clean_words2.append(q)
    elif word == "T":
        q = "T"
        clean_words2.append(q)

In [28]:
# lowercase Qless essay words
clean_words2_Qless =[]
for word in good_words2_Qless:
    if word != "Q":

        lowe= word.lower()
        clean_words2_Qless.append(lowe)

In [21]:
# save the essay words to csv
ess_df = pd.DataFrame({'Words':clean_words2})
ess_df.to_csv("Q T Essay Human.csv", index=False)

In [30]:
# save the Qless clean words to csv
ess_df_Qx = pd.DataFrame({'Words':clean_words2_Qless})
ess_df_Qx.to_csv("Qless Essay Human Words Cleanish .csv", index=False)


In [46]:
# Qless Essay Phrase analysis


# initialize collocation for essays 'e' text QLESS
import nltk
from nltk.collocations import *

# init nltk measures
bigram_measures_e1_Qx = nltk.collocations.BigramAssocMeasures()
trigram_measures_e2_Qx = nltk.collocations.TrigramAssocMeasures()
quadgram_measures_e3_Qx = nltk.collocations.QuadgramAssocMeasures()

# find phrases 
finder_e1_Qx = BigramCollocationFinder.from_words(clean_words2_Qless)
finder_e2_Qx = TrigramCollocationFinder.from_words(clean_words2_Qless)
finder_e3_Qx =QuadgramCollocationFinder.from_words(clean_words2_Qless)

# only phrases appearing 10+ times
finder_e1_Qx.apply_freq_filter(10)
finder_e2_Qx.apply_freq_filter(10)
finder_e3_Qx.apply_freq_filter(10)


# define phrase counts
bigram_freq_e1_Qx = finder_e1_Qx.ngram_fd.items()
trigram_freq_e2_Qx = finder_e2_Qx.ngram_fd.items()
quadgram_freq_e3_Qx = finder_e3_Qx.ngram_fd.items()

# define pmis
bigram_pmi_e1_Qx = [i for i in finder_e1_Qx.score_ngrams(bigram_measures_e1_Qx.pmi)]
trigram_pmi_e2_Qx = [i for i in finder_e2_Qx.score_ngrams(trigram_measures_e2_Qx.pmi)]
quadgram_pmi_e3_Qx = [i for i in finder_e3_Qx.score_ngrams(quadgram_measures_e3_Qx.pmi)]

# bigram list creation
pmi_list_e1_Qx =[]
count_list_e1_Qx =  []
phrase_list_e1_Qx =[]

for phrase , pmi in bigram_pmi_e1_Qx:
    for item in bigram_freq_e1_Qx:
        bigram, count = item
        if bigram == phrase:
            pmi_list_e1_Qx.append(pmi) # pmi for the bigram  = phrase
            count_list_e1_Qx.append(count)  # count for the phrase = bigram 
            phrase_list_e1_Qx.append(phrase) # phrase = bigram
            

#trigram list creation
pmi_list_e2_Qx = []
count_list_e2_Qx =[]
phrase_list_e2_Qx =[]

for phrase, pmi in trigram_pmi_e2_Qx:
    for item in trigram_freq_e2_Qx:
        bigram, count =item
        if bigram == phrase:
            pmi_list_e2_Qx.append(pmi)
            count_list_e2_Qx.append(count)
            phrase_list_e2_Qx.append(phrase)

# quadgram list creation
pmi_list_e3_Qx =[]
count_list_e3_Qx =[]
phrase_list_e3_Qx =[]

for phrase, pmi in quadgram_pmi_e3_Qx:
    for item in quadgram_freq_e3_Qx:
        quadgram, count =item
        if quadgram == phrase:
            pmi_list_e3_Qx.append(pmi)
            count_list_e3_Qx.append(count)
            phrase_list_e3_Qx.append(phrase)

# create dataframes
df_bigram_e1_Qless = pd.DataFrame({'Phrase':phrase_list_e1_Qx , 'Count':count_list_e1_Qx , 'PMI':pmi_list_e1_Qx}) 
df_trigram_e2_Qless = pd.DataFrame({'Phrase':phrase_list_e2_Qx , 'Count': count_list_e2_Qx , 'PMI':pmi_list_e2_Qx}) 
df_quadgram_e3_Qless = pd.DataFrame({'Phrase':phrase_list_e3_Qx , 'Count': count_list_e3_Qx , 'PMI': pmi_list_e3_Qx})

In [34]:
# WITH Q

# initialize collocation for essays 'e' text
import nltk
from nltk.collocations import *

# init nltk measures
bigram_measures_e1 = nltk.collocations.BigramAssocMeasures()
trigram_measures_e2 = nltk.collocations.TrigramAssocMeasures()
quadgram_measures_e3 = nltk.collocations.QuadgramAssocMeasures()

# find phrases 
finder_e1 = BigramCollocationFinder.from_words(clean_words2)
finder_e2 = TrigramCollocationFinder.from_words(clean_words2)
finder_e3 =QuadgramCollocationFinder.from_words(clean_words2)

# only phrases appearing 10+ times
finder_e1.apply_freq_filter(10)
finder_e2.apply_freq_filter(10)
finder_e3.apply_freq_filter(10)


# define phrase counts
bigram_freq_e1 = finder_e1.ngram_fd.items()
trigram_freq_e2 = finder_e2.ngram_fd.items()
quadgram_freq_e3 = finder_e3.ngram_fd.items()

# define pmis
bigram_pmi_e1 = [i for i in finder_e1.score_ngrams(bigram_measures_e1.pmi)]
trigram_pmi_e2 = [i for i in finder_e2.score_ngrams(trigram_measures_e2.pmi)]
quadgram_pmi_e3 = [i for i in finder_e3.score_ngrams(quadgram_measures_e3.pmi)]

# bigram list creation
pmi_list_e1 =[]
count_list_e1 =  []
phrase_list_e1 =[]

for phrase , pmi in bigram_pmi_e1:
    for item in bigram_freq_e1:
        bigram, count = item
        if bigram == phrase:
            pmi_list_e1.append(pmi) # pmi for the bigram  = phrase
            count_list_e1.append(count)  # count for the phrase = bigram 
            phrase_list_e1.append(phrase) # phrase = bigram
            

#trigram list creation
pmi_list_e2 = []
count_list_e2 =[]
phrase_list_e2 =[]

for phrase, pmi in trigram_pmi_e2:
    for item in trigram_freq_e2:
        bigram, count =item
        if bigram == phrase:
            pmi_list_e2.append(pmi)
            count_list_e2.append(count)
            phrase_list_e2.append(phrase)

# quadgram list creation
pmi_list_e3 =[]
count_list_e3 =[]
phrase_list_e3 =[]

for phrase, pmi in quadgram_pmi_e3:
    for item in quadgram_freq_e3:
        quadgram, count =item
        if quadgram == phrase:
            pmi_list_e3.append(pmi)
            count_list_e3.append(count)
            phrase_list_e3.append(phrase)

# create dataframes
df_bigram_e1 = pd.DataFrame({'Phrase':phrase_list_e1 , 'Count':count_list_e1 , 'PMI':pmi_list_e1}) 
df_trigram_e2 = pd.DataFrame({'Phrase':phrase_list_e2 , 'Count': count_list_e2 , 'PMI':pmi_list_e2}) 
df_quadgram_e3 = pd.DataFrame({'Phrase':phrase_list_e3 , 'Count': count_list_e3 , 'PMI': pmi_list_e3})

In [32]:
# create dataframes Qless
df_bigram_e1_Qless = pd.DataFrame({'Phrase':phrase_list_e1_Qx , 'Count':count_list_e1_Qx , 'PMI':pmi_list_e1_Qx}) 
df_trigram_e2_Qless = pd.DataFrame({'Phrase':phrase_list_e2_Qx , 'Count': count_list_e2_Qx , 'PMI':pmi_list_e2_Qx}) 
df_quadgram_e3_Qless = pd.DataFrame({'Phrase':phrase_list_e3_Qx , 'Count': count_list_e3_Qx , 'PMI': pmi_list_e3_Qx})

# HC3

In [ ]:
# HC3 datasets 
import json

with open(r"C:\Users\Admin\HC3 json file") as f:
  data = json.load(f)

# parse the human
human_answers = []

for row in data['rows']:
  human = row['row']['human_answers']
  human_answers.append(human)

# flatten answers
flat_human = [item for sublist in human_answers for item in sublist]
flat_human 

In [4]:
# clean HC3
import nltk 

def preprocess(sent):
    sent = nltk.word_tokenize(sent)
    sent = nltk.pos_tag(sent)
    return sent

clean3 = []
try:
  for sentence in flat_human:

    # process sentences
    cleane = preprocess(sentence)
    clean3.append(cleane)

except KeyError:
  print("Column 'Data' not found")

In [11]:
# HC3 Qless
good_words3_Qless =[]
for pair in clean3:

    for word, tag in pair:
        if tag != "NNP" and tag != ":" and tag != "''" and tag != "``" and tag != ".":
            good_words3_Qless.append(word)

            
clean_words3_Qless =[]
for word in good_words3_Qless:
    

    lowe= word.lower()
    clean_words3_Qless.append(lowe)
    

In [7]:
# WITH T FOR PUNCT
good_words3 =[]
for pair in clean3:

    for word, tag in pair:
        if tag != "NNP" and tag != ":" and tag != "''" and tag != "``" and tag != ".":
            good_words3.append(word)

        elif tag == "NNP": 
            q = "Q"
            good_words3.append(q)

        elif tag == ":":
            q = "T" 
            good_words3.append(q)

        elif tag == ".":
            q = "T"
            good_words3.append(q)
            
clean_words3 =[]
for word in good_words3:
    if word != "Q" and word != "T":

        lowe= word.lower()
        clean_words3.append(lowe)
        
    elif word == "Q":
        q ="Q"
        clean_words3.append(q)
    elif word == "T":
        q = "T"
        clean_words3.append(q)

In [ ]:
clean_words3

In [10]:
# save the HC3 words to csv
import pandas as pd
hc3_df = pd.DataFrame({'Words':clean_words3})
hc3_df.to_csv("Q T HC3 Human.csv", index=False)

In [12]:
# save QLess HC3
# save the HC3 words to csv
hc3_df_Qx = pd.DataFrame({'Words':clean_words3_Qless})
hc3_df_Qx.to_csv("HC3 Human Clean.csv", index=False)

# Observations
> find number  of proper nouns in each of the following: human-essay = 10747 | human-HC3 = 1201 | and human-reddit = 44661  | 56,609 
>> count original number of words in each uncleaned corpus | human-HC3 = 35969  | human-reddit = 909307 | human-essay = 1143024
>>> count number of T's = periods  | in human-essays= 45613 |  human-HC3= 2007 |  human reddit= 40716  
* need original word length for ratio of words to periods 

In [37]:
import mean_sentence_length_function

In [41]:
# import mean_sentence_length_function
from mean_sentence_length_function import *

# get number of T = periods in each text
ess_Ts = ess_df.value_counts().get('T',0)
HC_Ts = hc3_df.value_counts().get('T',0)
red_Ts = red_df.value_counts().get('T',0)

HC_mean_sent = average_sent_length(hc3_df,HC_Ts)
ess_mean_sent = average_sent_length(ess_df,ess_Ts)
red_mean_sent = average_sent_length(red_df,red_Ts)

In [43]:
print(HC_mean_sent)
print(ess_mean_sent)
print(red_mean_sent)

16.92177379172895
24.05917172735843
21.332915807053737


In [44]:
# AGGREGATE AVERAGE
(16.92177379172895 +24.05917172735843 + 21.332915807053737)/3

20.771287108713704

>>Average human sentence length is 20.771287108713704 words

In [30]:
hc3_df.value_counts().head(20)

Words
T        2007
the      1601
,        1414
Q        1201
to        972
a         869
and       804
of        689
is        551
it        550
that      498
in        460
you       360
are       304
for       294
's        293
they      284
)         231
be        227
or        218
Name: count, dtype: int64

In [ ]:
ess_df.value_counts().head(20)

In [32]:
red_df.value_counts().head(20)

Words
the      46435
Q        44661
T        40716
,        39806
of       23140
to       21875
and      19646
a        18832
in       15232
that     12063
is       11396
it       10238
you       6907
for       6697
)         6187
this      6075
as        6062
(         6055
i         6025
was       5707
Name: count, dtype: int64

>>> Now count number of words in text

In [33]:
def count_words(string):
    st1 = string.strip()
    count = 1
    for i in st1:
        if i == " ":
            count +=1
    return count

In [36]:
len(ess_df)

1143024

In [35]:
len(hc3_df)

35969

In [34]:
len(red_df)

909307

In [41]:
# Qless SAME LIST NAMES DIFF Dataframe
# initialize collocation for HC3 'h' text
import nltk
from nltk.collocations import *

# init nltk measures
bigram_measures_h1_Qx = nltk.collocations.BigramAssocMeasures()
trigram_measures_h2_Qx = nltk.collocations.TrigramAssocMeasures()
quadgram_measures_h3_Qx = nltk.collocations.QuadgramAssocMeasures()

# find phrases 
finder_h1_Qx = BigramCollocationFinder.from_words(clean_words3_Qless)
finder_h2_Qx= TrigramCollocationFinder.from_words(clean_words3_Qless)
finder_h3_Qx =QuadgramCollocationFinder.from_words(clean_words3_Qless)

# only phrases appearing 10+ times
finder_h1_Qx.apply_freq_filter(10)
finder_h2_Qx.apply_freq_filter(10)
finder_h3_Qx.apply_freq_filter(10)


# define phrase counts
bigram_freq_h1_Qx = finder_h1_Qx.ngram_fd.items()
trigram_freq_h2_Qx = finder_h2_Qx.ngram_fd.items()
quadgram_freq_h3_Qx = finder_h3_Qx.ngram_fd.items()

# define pmis
bigram_pmi_h1_Qx = [i for i in finder_h1_Qx.score_ngrams(bigram_measures_h1_Qx.pmi)]
trigram_pmi_h2_Qx = [i for i in finder_h2_Qx.score_ngrams(trigram_measures_h2_Qx.pmi)]
quadgram_pmi_h3_Qx = [i for i in finder_h3_Qx.score_ngrams(quadgram_measures_h3_Qx.pmi)]

# bigram list creation
pmi_list_h1_Qx =[]
count_list_h1_Qx =  []
phrase_list_h1_Qx =[]

for phrase , pmi in bigram_pmi_h1_Qx:
    for item in bigram_freq_h1_Qx:
        bigram, count = item
        if bigram == phrase:
            pmi_list_h1_Qx.append(pmi) # pmi for the bigram  = phrase
            count_list_h1_Qx.append(count)  # count for the phrase = bigram 
            phrase_list_h1_Qx.append(phrase) # phrase = bigram
            

#trigram list creation
pmi_list_h2_Qx = []
count_list_h2_Qx =[]
phrase_list_h2_Qx =[]

for phrase, pmi in trigram_pmi_h2_Qx:
    for item in trigram_freq_h2_Qx:
        bigram, count =item
        if bigram == phrase:
            pmi_list_h2_Qx.append(pmi)
            count_list_h2_Qx.append(count)
            phrase_list_h2_Qx.append(phrase)

# quadgram list creation
pmi_list_h3_Qx =[]
count_list_h3_Qx =[]
phrase_list_h3_Qx =[]

for phrase, pmi in quadgram_pmi_h3_Qx:
    for item in quadgram_freq_h3_Qx:
        quadgram, count =item
        if quadgram == phrase:
            pmi_list_h3_Qx.append(pmi)
            count_list_h3_Qx.append(count)
            phrase_list_h3_Qx.append(phrase)

# create dataframes
df_bigram_h1_Qless = pd.DataFrame({'Phrase':phrase_list_h1_Qx , 'Count':count_list_h1_Qx , 'PMI':pmi_list_h1_Qx}) 
df_trigram_h2_Qless = pd.DataFrame({'Phrase':phrase_list_h2_Qx , 'Count': count_list_h2_Qx , 'PMI':pmi_list_h2_Qx}) 
df_quadgram_h3_Qless = pd.DataFrame({'Phrase':phrase_list_h3_Qx , 'Count': count_list_h3_Qx , 'PMI': pmi_list_h3_Qx})

In [46]:
clean_words3

['basically',
 'there',
 'are',
 'many',
 'categories',
 'of',
 'Q',
 'Q',
 'T',
 'replace',
 'Q',
 'Q',
 'by',
 'something',
 'like',
 'Q',
 'and',
 'every',
 'best',
 'seller',
 'book',
 'is',
 'basically',
 'an',
 'oscar',
 'T',
 'winning',
 'book',
 'T',
 'Q',
 'not',
 'have',
 'won',
 'the',
 'Q',
 'film',
 ',',
 'but',
 'even',
 'if',
 'you',
 'won',
 'the',
 'best',
 'director',
 'or',
 'best',
 'script',
 ',',
 'you',
 "'re",
 'still',
 'an',
 'oscar',
 'T',
 'winning',
 'film',
 'T',
 'same',
 'thing',
 'for',
 'best',
 'sellers',
 'T',
 'also',
 ',',
 'Q',
 'the',
 'rankings',
 'change',
 'every',
 'week',
 'or',
 'something',
 'like',
 'that',
 'T',
 'some',
 'you',
 'might',
 'not',
 'be',
 'best',
 'seller',
 'one',
 'week',
 ',',
 'but',
 'you',
 'may',
 'be',
 'the',
 'next',
 'week',
 'T',
 'i',
 'guess',
 'even',
 'if',
 'you',
 'do',
 "n't",
 'stay',
 'there',
 'for',
 'long',
 ',',
 'you',
 'still',
 'achieved',
 'the',
 'status',
 'T',
 'Q',
 ',',
 '#',
 '1',
 'best

In [47]:
# initialize collocation for HC3 'h' text
import nltk
from nltk.collocations import *

# init nltk measures
bigram_measures_h1 = nltk.collocations.BigramAssocMeasures()
trigram_measures_h2 = nltk.collocations.TrigramAssocMeasures()
quadgram_measures_h3 = nltk.collocations.QuadgramAssocMeasures()

# find phrases 
finder_h1 = BigramCollocationFinder.from_words(clean_words3)
finder_h2 = TrigramCollocationFinder.from_words(clean_words3)
finder_h3 =QuadgramCollocationFinder.from_words(clean_words3)

# only phrases appearing 10+ times
finder_h1.apply_freq_filter(10)
finder_h2.apply_freq_filter(10)
finder_h3.apply_freq_filter(10)


# define phrase counts
bigram_freq_h1 = finder_h1.ngram_fd.items()
trigram_freq_h2 = finder_h2.ngram_fd.items()
quadgram_freq_h3 = finder_h3.ngram_fd.items()

# define pmis
bigram_pmi_h1 = [i for i in finder_h1.score_ngrams(bigram_measures_h1.pmi)]
trigram_pmi_h2 = [i for i in finder_h2.score_ngrams(trigram_measures_h2.pmi)]
quadgram_pmi_h3 = [i for i in finder_h3.score_ngrams(quadgram_measures_h3.pmi)]

# bigram list creation
pmi_list_h1 =[]
count_list_h1 =  []
phrase_list_h1 =[]

for phrase , pmi in bigram_pmi_h1:
    for item in bigram_freq_h1:
        bigram, count = item
        if bigram == phrase:
            pmi_list_h1.append(pmi) # pmi for the bigram  = phrase
            count_list_h1.append(count)  # count for the phrase = bigram 
            phrase_list_h1.append(phrase) # phrase = bigram
            

#trigram list creation
pmi_list_h2 = []
count_list_h2 =[]
phrase_list_h2 =[]

for phrase, pmi in trigram_pmi_h2:
    for item in trigram_freq_h2:
        bigram, count =item
        if bigram == phrase:
            pmi_list_h2.append(pmi)
            count_list_h2.append(count)
            phrase_list_h2.append(phrase)

# quadgram list creation
pmi_list_h3 =[]
count_list_h3 =[]
phrase_list_h3 =[]

for phrase, pmi in quadgram_pmi_h3:
    for item in quadgram_freq_h3:
        quadgram, count =item
        if quadgram == phrase:
            pmi_list_h3.append(pmi)
            count_list_h3.append(count)
            phrase_list_h3.append(phrase)

# create dataframes
df_bigram_h1 = pd.DataFrame({'Phrase':phrase_list_h1 , 'Count':count_list_h1 , 'PMI':pmi_list_h1}) 
df_trigram_h2 = pd.DataFrame({'Phrase':phrase_list_h2 , 'Count': count_list_h2 , 'PMI':pmi_list_h2}) 
df_quadgram_h3 = pd.DataFrame({'Phrase':phrase_list_h3 , 'Count': count_list_h3 , 'PMI': pmi_list_h3})

In [51]:
len(df_quadgram_h3)

8

In [43]:
df_bigram_h1

Phrase  Count        PMI
0     (grand, jury)     16  10.218587
1    (rather, than)     14   8.484440
2       (at, least)     11   8.138571
3           (i, 'm)     21   7.768144
4         (ca, n't)     27   7.327112
..              ...    ...        ...
270         (,, to)     13  -1.555473
271          (a, Q)     24  -1.691242
272         (Q, to)     24  -1.852842
273         (to, Q)     24  -1.852842
274         (Q, of)     15  -2.034462

[275 rows x 3 columns]

In [44]:
# concatenate all dfs (9) to evaluate most common and highest pmi across all human and phrase sizes

merged_df = pd.concat([df_bigram_r1,df_bigram_e1,df_bigram_h1,df_trigram_e2,df_trigram_r2,df_trigram_h2,df_quadgram_r3,df_quadgram_h3,df_quadgram_e3])


In [ ]:
df

In [50]:
# concatenate all QLESSS dfs (9) to evaluate most common and highest pmi across all human and phrase sizes

merged_df_Qx = pd.concat([df_bigram_r1_Qx,df_bigram_e1_Qless,df_bigram_h1_Qless,df_trigram_e2_Qless,df_trigram_r2_Qx,df_trigram_h2_Qless,df_quadgram_r3_Qx,df_quadgram_h3_Qless,df_quadgram_e3_Qless])


In [53]:
merged_df_Qx

Phrase  Count        PMI
0            (vice, versa)   13.0  15.545247
1                (gon, na)   17.0  15.330234
2         (belly, dancing)   10.0  14.745272
3                 (et, al)   36.0  13.691517
4         (voter, turnout)   11.0  13.633836
...                    ...    ...        ...
3289  (to, the, school, ,)   10.0   4.936693
3290        (,, ,, ,, and)   27.0   4.816196
3291    (you, ,, and, you)   12.0   4.663686
3292      (,, and, to, be)   10.0   4.521938
3293      (to, be, ,, and)   10.0   4.521938

[41470 rows x 3 columns]

In [62]:
good_phrase_Qx =[]
for phrase in merged_df_Qx['Phrase']:
    clean = ' '.join(phrase)
    good_phrase_Qx.append(clean)

In [64]:
merged_df_Qx['Phrase'] = good_phrase_Qx

In [65]:
merged_df_Qx

Phrase  Count        PMI
0          vice versa   13.0  15.545247
1              gon na   17.0  15.330234
2       belly dancing   10.0  14.745272
3               et al   36.0  13.691517
4       voter turnout   11.0  13.633836
...               ...    ...        ...
3289  to the school ,   10.0   4.936693
3290        , , , and   27.0   4.816196
3291    you , and you   12.0   4.663686
3292      , and to be   10.0   4.521938
3293      to be , and   10.0   4.521938

[41470 rows x 3 columns]

In [66]:
# save Qx to csvc
merged_df_Qx.to_csv('NO Q BI TRI QUAD HUMAN GRAMS.csv')

In [67]:
merged_df.to_csv('Q BI TRI QUAD HUMAN GRAMS.csv')

In [37]:
total_rows =len(df_bigram_e1)+len(df_bigram_r1)+len(df_bigram_h1)+len(df_quadgram_h3)+len(df_quadgram_e3)+len(df_quadgram_r3) +len(df_trigram_e2)+len(df_trigram_r2)+len(df_trigram_h2)

In [38]:
total_rows

46654

In [35]:
merged_df


Phrase  Count        PMI
0        (vice, versa)     13  15.687493
1            (gon, na)     17  15.472480
2     (belly, dancing)     10  14.887517
3             (et, al)     36  13.833762
4     (voter, turnout)     11  13.776081
...                ...    ...        ...
4068    (and, Q, Q, Q)     15   2.059183
4069      (,, Q, Q, Q)     16   1.953025
4070    (Q, the, Q, Q)     12   1.498807
4071    (Q, Q, Q, and)     10   1.474220
4072     (to, Q, Q, Q)     14   1.387394

[46654 rows x 3 columns]

In [61]:
merged_df.to_csv('bi tri quad human metrics.csv', index=False)

In [56]:
good_phrase =[]
for phrase in merged_df['Phrase']:
    clean = ' '.join(phrase)
    good_phrase.append(clean)

In [57]:
merged_df['Phrase'] = good_phrase
# run to_csv cell block above again

In [58]:
# now explore
merged_df = merged_df.sort_values('PMI',ascending=False)


In [63]:
# remove the firs two rows which are context specific
merged_df = merged_df.drop(axis=0,labels=[0,1])

In [59]:
merged_df.tail(20)

Phrase  Count       PMI
9622       of ,     30 -5.077501
14333     to is     19 -5.103449
14334    to can     13 -5.132106
14335   they to     19 -5.138809
14336  the they     15 -5.146041
14337     the a     20 -5.163714
14338   and and     22 -5.163801
14339   can the     10 -5.176812
14340     to to     44 -5.308308
14341  the that     15 -5.310682
14342       a a     11 -5.411723
14343    the is     12 -5.432608
14344     of to     12 -5.438868
14345       i ,     11 -5.443890
14346    to for     11 -5.484278
14347  they and     10 -5.492556
14348     a the     11 -6.026210
14349     to in     10 -6.165500
14350    they Q     10 -6.401111
9623    the the     25 -6.567586

### quadgrams have high pmi and bigrams have negative ; i.e. higher joint prob than indiv vs. higher indiv. porb than joint prob

In [67]:
merged_df.head(20)

Phrase  Count        PMI
2        formed by influences beyond     20  32.803633
3         seek guidance from experts     45  32.645959
2   better familiarize yourself with     53  31.547293
4       retain information as easily     10  31.281380
5      influences beyond our control     25  31.198736
3    providing follow up information     11  31.168131
6    schools offer distance learning     31  30.845589
4         further derail this thread     10  30.669236
5        provide users with in-depth     10  30.572888
7     character formed by influences     10  30.426663
8       tasks without having contact     17  30.330385
9             small acts of kindness     19  30.186502
6        someone capable of engaging     15  29.955864
10     seeking multiple opinions can     21  29.884351
11               setting our aim too     21  29.786959
12           consisting of ten hours     19  29.713366
13       play games without speaking     10  29.641778
14       limitation of human contact     29  29.595761
7     informed response from someone     15  29.582138
15        does inactivity also serve     19  29.518296

In [71]:
merged_df.sort_values('Count', ascending = False)

Phrase  Count        PMI
6599               Q Q  19575   1.288013
7726             the Q   6517   0.579915
9495               Q Q   6170   1.150711
3690             Q Q Q   5782   2.941489
4917            of the   5533   2.227228
...                ...    ...        ...
3298        , the best     10   3.977374
1012      young age it     10  11.349398
7320            be any     10   0.851580
10317     reason would     10   0.852112
9735   in everything Q     10   3.910095

[46636 rows x 3 columns]

# top count is significant becausr shows humans use proper nouns a lot 1 , disregard pMI . Maybe add Q's to chatgpt to compare

Bi and Tri Gram notebook conatins code that evaluates chatgpt phrases with and without Q 

# the prob with putting Q in place of punct and proper nouns is that pmi is not accurate (i.e. prob of Q )
